In [59]:
import pandas as pd
import numpy as np
import os

# Elo
Run Elo over a data set.

In [95]:
start_year = 2000 # 1968
end_year = 2018
base_dir = r"C:/Users/Paul/tennis_atp"
filename_label = r"atp_matches_%d.csv"

def process_year_df(df_year):
    df = df_year.loc[:, ['tourney_name', 'tourney_level', 'tourney_date', 'match_num', 'score', 'round', 'winner_name', 'loser_name']]
    # Put in chronological order.
    df = df.sort_values(['tourney_date', 'tourney_name', 'match_num'], ascending=[True, True, True])
    return df

In [96]:
# Read the match data.
df = None
for year in range(start_year, end_year + 1):
    filename = os.path.join(base_dir, filename_label % year)
    df_year = pd.read_csv(filename)
    df_year = process_year_df(df_year)
#     df_year = df_year.loc[df_year['tourney_name'] == 'Montpellier']
    print(filename)
    print(df_year[0:300])
    
    if df is None:
        df = df_year
    else:
        df = pd.concat([df, df_year])

C:/Users/Paul/tennis_atp\atp_matches_2000.csv
                     tourney_name tourney_level  tourney_date  match_num  \
674                      Adelaide             A      20000103          1   
675                      Adelaide             A      20000103          2   
676                      Adelaide             A      20000103          3   
677                      Adelaide             A      20000103          4   
678                      Adelaide             A      20000103          5   
679                      Adelaide             A      20000103          6   
680                      Adelaide             A      20000103          7   
681                      Adelaide             A      20000103          8   
682                      Adelaide             A      20000103          9   
683                      Adelaide             A      20000103         10   
684                      Adelaide             A      20000103         11   
685                      Adelaide         

C:/Users/Paul/tennis_atp\atp_matches_2004.csv
                     tourney_name tourney_level  tourney_date  match_num  \
786                      Adelaide             A      20040105          1   
787                      Adelaide             A      20040105          2   
788                      Adelaide             A      20040105          3   
789                      Adelaide             A      20040105          4   
790                      Adelaide             A      20040105          5   
791                      Adelaide             A      20040105          6   
792                      Adelaide             A      20040105          7   
793                      Adelaide             A      20040105          8   
794                      Adelaide             A      20040105          9   
795                      Adelaide             A      20040105         10   
796                      Adelaide             A      20040105         11   
797                      Adelaide         

[300 rows x 8 columns]
C:/Users/Paul/tennis_atp\atp_matches_2008.csv
         tourney_name tourney_level  tourney_date  match_num  \
62           Adelaide             A      20071231          1   
63           Adelaide             A      20071231          2   
64           Adelaide             A      20071231          3   
65           Adelaide             A      20071231          4   
66           Adelaide             A      20071231          5   
67           Adelaide             A      20071231          6   
68           Adelaide             A      20071231          7   
69           Adelaide             A      20071231          8   
70           Adelaide             A      20071231          9   
71           Adelaide             A      20071231         10   
72           Adelaide             A      20071231         11   
73           Adelaide             A      20071231         12   
74           Adelaide             A      20071231         13   
75           Adelaide             A

[300 rows x 8 columns]
C:/Users/Paul/tennis_atp\atp_matches_2011.csv
         tourney_name tourney_level  tourney_date  match_num  \
1802         Brisbane             A      20110102          1   
1803         Brisbane             A      20110102          2   
1804         Brisbane             A      20110102          3   
1805         Brisbane             A      20110102          4   
1806         Brisbane             A      20110102          5   
1807         Brisbane             A      20110102          6   
1808         Brisbane             A      20110102          7   
1809         Brisbane             A      20110102          8   
1810         Brisbane             A      20110102          9   
1811         Brisbane             A      20110102         10   
1812         Brisbane             A      20110102         11   
1813         Brisbane             A      20110102         12   
1814         Brisbane             A      20110102         13   
1815         Brisbane             A

C:/Users/Paul/tennis_atp\atp_matches_2014.csv
                     tourney_name tourney_level  tourney_date  match_num  \
1092                     Brisbane             A      20131229          1   
1093                     Brisbane             A      20131229          2   
1094                     Brisbane             A      20131229          3   
1095                     Brisbane             A      20131229          4   
1096                     Brisbane             A      20131229          5   
1097                     Brisbane             A      20131229          6   
1098                     Brisbane             A      20131229          7   
1099                     Brisbane             A      20131229          8   
1100                     Brisbane             A      20131229          9   
1101                     Brisbane             A      20131229         10   
1102                     Brisbane             A      20131229         11   
1103                     Brisbane         

[300 rows x 8 columns]
C:/Users/Paul/tennis_atp\atp_matches_2018.csv
                     tourney_name tourney_level  tourney_date  match_num  \
26                       Brisbane             A      20180101        271   
25                       Brisbane             A      20180101        272   
24                       Brisbane             A      20180101        273   
23                       Brisbane             A      20180101        275   
22                       Brisbane             A      20180101        276   
21                       Brisbane             A      20180101        277   
20                       Brisbane             A      20180101        278   
19                       Brisbane             A      20180101        279   
18                       Brisbane             A      20180101        280   
17                       Brisbane             A      20180101        282   
16                       Brisbane             A      20180101        283   
15                 

In [97]:
# Run Elo through the data.
# http://www.eloratings.net/about
# https://www.betfair.com.au/hub/better-betting/betting-strategies/tennis/tennis-elo-modelling/

start_elo = 1500
use_fte_K = True
if use_fte_K:
    def get_K(n_matches):
        return 250 / np.power(n_matches + 5, 0.4)
else:
    def get_K(n_matches): 
        return 20

from collections import defaultdict
# The Elo rating at any point in time.
elo_ratings = defaultdict(lambda: start_elo)
# The number of matches played by each player, at any point in time.
n_matches_played = defaultdict(lambda: 0)

for index, row in df.iterrows():
#     print(index, row)
    winner = row['winner_name']
    loser = row['loser_name']
    
    # The pre-match ratings.
    winner_rating = elo_ratings[winner]
    loser_rating = elo_ratings[loser]
        
    # The pre-match win expectancy.
    rating_diff = winner_rating - loser_rating
    winner_win_expectancy = 1 / (np.power(10, -rating_diff / 400) + 1)
    loser_win_expectancy = 1 - winner_win_expectancy
    
    # The post-match ratings.
    K_winner = get_K(n_matches_played[winner])
    K_loser = get_K(n_matches_played[loser])
    new_winner_rating = winner_rating + K_winner * (1 - winner_win_expectancy)
    new_loser_rating = loser_rating + K_loser * (0 - loser_win_expectancy)
    
#     print(winner_rating, loser_rating, rating_diff, win_expectancy)
#     print(winner, loser, new_winner_rating, new_loser_rating)
    print(winner, n_matches_played[winner], K_winner)
    print(loser, n_matches_played[loser], K_loser)
    print()
    
    elo_ratings[winner] = new_winner_rating
    elo_ratings[loser] = new_loser_rating
    
    n_matches_played[winner] += 1
    n_matches_played[loser] += 1
    
#     if index > 50:
#         break
    

Thomas Enqvist 0 131.32639022018836
Arnaud Clement 0 131.32639022018836

Roger Federer 0 131.32639022018836
Jens Knippschild 0 131.32639022018836

Jan Michael Gambill 0 131.32639022018836
Wayne Arthurs 0 131.32639022018836

Sebastien Grosjean 0 131.32639022018836
Andrew Ilie 0 131.32639022018836

Magnus Norman 0 131.32639022018836
Scott Draper 0 131.32639022018836

Richard Fromberg 0 131.32639022018836
Todd Woodbridge 0 131.32639022018836

James Sekulov 0 131.32639022018836
Gianluca Pozzi 0 131.32639022018836

Alberto Martin 0 131.32639022018836
Vincent Spadea 0 131.32639022018836

Lleyton Hewitt 0 131.32639022018836
Mark Woodforde 0 131.32639022018836

Dejan Petrovic 0 131.32639022018836
Stephane Huet 0 131.32639022018836

Christian Vinck 0 131.32639022018836
Paul Goldstein 0 131.32639022018836

Jason Stoltenberg 0 131.32639022018836
Dominik Hrbaty 0 131.32639022018836

Nicolas Escude 0 131.32639022018836
Paul Baccanello 0 131.32639022018836

Slava Dosedel 0 131.32639022018836
Ivan Lj

Mark Woodforde 3 108.81882041201551

Slava Dosedel 6 95.80384393390682
Paradorn Srichaphan 1 122.08983548264673

Tim Henman 4 103.81091163462644
Rainer Schuettler 6 95.80384393390682

Sebastien Grosjean 5 99.52679263837432
Michael Hill 1 122.08983548264673

Chris Woodruff 2 114.7891374898585
James Sekulov 3 108.81882041201551

Richard Fromberg 4 103.81091163462644
Axel Pretzsch 1 122.08983548264673

Adrian Voinea 5 99.52679263837432
Albert Portas 1 122.08983548264673

Lleyton Hewitt 11 82.46924442330588
Alex Corretja 5 99.52679263837432

Jonas Bjorkman 2 114.7891374898585
Jiri Vanek 3 108.81882041201551

Magnus Norman 10 84.62593986645679
Gianluca Pozzi 2 114.7891374898585

Francisco Clavet 3 108.81882041201551
Goran Ivanisevic 3 108.81882041201551

Wayne Ferreira 1 122.08983548264673
Thomas Johansson 3 108.81882041201551

Karim Alami 1 122.08983548264673
Michael Llodra 1 122.08983548264673

Nicolas Kiefer 5 99.52679263837432
Tomas Behrend 5 99.52679263837432

Arnaud Clement 4 103.8109

Roger Federer 10 84.62593986645679
Ivan Ljubicic 8 89.61127730838588

Fabrice Santoro 8 89.61127730838588
Thierry Guardiola 2 114.7891374898585

Sebastien Grosjean 9 86.99389867440918
Andreas Vinciguerra 7 92.52679312178833

Marc Rosset 7 92.52679312178833
Goran Ivanisevic 6 95.80384393390682

Roger Federer 11 82.46924442330588
Fabrice Santoro 9 86.99389867440918

Marc Rosset 8 89.61127730838588
Sebastien Grosjean 10 84.62593986645679

Marc Rosset 9 86.99389867440918
Roger Federer 12 80.49343113115424

Mark Woodforde 4 103.81091163462644
Scott Humphries 0 131.32639022018836

Magnus Larsson 0 131.32639022018836
Martin Rodriguez 1 122.08983548264673

Ville Liukko 0 131.32639022018836
Laurence Tieleman 3 108.81882041201551

Wayne Ferreira 4 103.81091163462644
Jeff Salzenstein 0 131.32639022018836

Michael Chang 6 95.80384393390682
Paradorn Srichaphan 3 108.81882041201551

Cecil Mamiit 1 122.08983548264673
Julian Alonso 1 122.08983548264673

Sargis Sargsian 2 114.7891374898585
John Van Lot

Andreas Vinciguerra 8 89.61127730838588
Christophe Rochus 6 95.80384393390682

Martin Damm 7 92.52679312178833
Kristian Pless 0 131.32639022018836

George Bastl 7 92.52679312178833
Mikael Tillstrom 12 80.49343113115424

Goran Ivanisevic 10 84.62593986645679
David Prinosil 3 108.81882041201551

Ivan Ljubicic 10 84.62593986645679
Petr Luxa 1 122.08983548264673

Tomas Behrend 7 92.52679312178833
Marc Rosset 15 75.42720420681452

Magnus Larsson 8 89.61127730838588
Wayne Arthurs 3 108.81882041201551

Roger Federer 16 73.96943318286598
Filip Dewulf 4 103.81091163462644

Fredrik Jonsson 5 99.52679263837432
Axel Pretzsch 5 99.52679263837432

Gianluca Pozzi 4 103.81091163462644
Jan Siemerink 6 95.80384393390682

Ville Liukko 2 114.7891374898585
Thomas Johansson 8 89.61127730838588

Marat Safin 7 92.52679312178833
Jan Kroslak 7 92.52679312178833

Jonas Bjorkman 9 86.99389867440918
Ivo Heuberger 2 114.7891374898585

Andreas Vinciguerra 9 86.99389867440918
Rainer Schuettler 14 76.99075318959495

M

Jonas Bjorkman 12 80.49343113115424

Goran Ivanisevic 14 76.99075318959495
David Prinosil 4 103.81091163462644

Arnaud Clement 12 80.49343113115424
Chris Woodruff 16 73.96943318286598

Nicolas Massu 8 89.61127730838588
Arnaud Di Pasquale 8 89.61127730838588

Jan Michael Gambill 12 80.49343113115424
Slava Dosedel 13 78.67395927457515

Cyril Saulnier 5 99.52679263837432
Thomas Johansson 11 82.46924442330588

Wayne Black 8 89.61127730838588
Alberto Berasategui 5 99.52679263837432

Gaston Gaudio 15 75.42720420681452
Hernan Gumy 10 84.62593986645679

Mardy Fish 0 131.32639022018836
Galo Blanco 7 92.52679312178833

Paul Goldstein 12 80.49343113115424
Christian Ruud 0 131.32639022018836

Guillermo Canas 8 89.61127730838588
Ivan Ljubicic 13 78.67395927457515

Jim Courier 7 92.52679312178833
David Nalbandian 0 131.32639022018836

George Bastl 9 86.99389867440918
Tuomas Ketola 3 108.81882041201551

Jerome Golmard 17 72.60573669299964
Daniel Vacek 12 80.49343113115424

Xavier Malisse 4 103.810911

...

Julien Benneteau 548 19.991710592318235
Marin Cilic 666 18.50337713150815

John Isner 578 19.57368463248534
Juan Martin Del Potro 544 20.04984737007336

Filip Krajinovic 52 49.612380563965935
Rafael Nadal 1068 15.335576963296486

Jack Sock 251 27.204705103003878
Julien Benneteau 549 19.97726832021527

Filip Krajinovic 53 49.26843999301356
John Isner 579 19.560271105909777

Jack Sock 252 27.162313620300182
Filip Krajinovic 54 48.932702723139236

David Goffin 323 24.637150199991204
Rafael Nadal 1069 15.329863792803925

Jack Sock 253 27.120152437104903
Marin Cilic 667 18.492358295716496

Jack Sock 254 27.078219416888345
Alexander Zverev 184 30.715337167239625

Alexander Zverev 185 30.650570911092288
Marin Cilic 668 18.481362391951308

Roger Federer 1357 13.940205168284244
Jack Sock 255 27.03651245109243

Roger Federer 1358 13.93611323148411
Marin Cilic 669 18.470389338519123

Roger Federer 1359 13.932025495543323
Alexander Zverev 186 30.586280129821247

Grigor Dimitrov 415 22.317230166985

Roberto Cid 9 86.99389867440918

Aisam Ul Haq Qureshi 66 45.439826993564886
Soon Woo Kwon 2 114.7891374898585

Aqeel Khan 60 47.07330228772238
Seong Chan Hong 4 103.81091163462644

M Abid Ali Khan Akbar 3 108.81882041201551
Minjong Park 0 131.32639022018836

Lloyd George Muirhead Harris 12 80.49343113115424
Edan Leshem 3 108.81882041201551

Dudi Sela 323 24.637150199991204
Nicolaas Scholtz 11 82.46924442330588

Dudi Sela 324 24.607168859958595
Lloyd George Muirhead Harris 13 78.67395927457515

Edan Leshem 4 103.81091163462644
Nicolaas Scholtz 12 80.49343113115424

Mikael Ymer 10 84.62593986645679
Sergiy Stakhovsky 359 23.63194434714334

Elias Ymer 38 55.5331906417378
Artem Smirnov 8 89.61127730838588

Sergiy Stakhovsky 360 23.606025008737774
Elias Ymer 39 55.02485896463572

Mikael Ymer 11 82.46924442330588
Artem Smirnov 9 86.99389867440918

Alexander Zverev 190 30.333754259423387
Alex De Minaur 17 72.60573669299964

Nick Kyrgios 179 31.04651658534805
Jan Lennard Struff 162 32.274046486

Yuichi Sugita 95 39.622329811527834

Filip Krajinovic 56 48.28453737272083
Felix Auger Aliassime 0 131.32639022018836

Damir Dzumhur 151 33.165776467568904
Marius Copil 92 40.10802850874502

Andrey Rublev 76 43.10682149764887
Lucas Pouille 157 32.66886173679649

David Goffin 337 24.228669523828245
Nicolas Mahut 387 22.941699234347126

Feliciano Lopez 869 16.646979151113126
Martin Klizan 247 27.376617765787945

Viktor Troicki 541 20.09384054518118
Jan Lennard Struff 163 32.1970658620195

Tomas Berdych 946 16.094141002085347
Mischa Zverev 268 26.513981557175697

Daniil Medvedev 65 45.69837873636395
Gilles Muller 425 22.108161398190187

Pierre Hugues Herbert 87 40.966124236308616
Richard Gasquet 784 17.342400337215135

Andreas Seppi 686 18.28726632398137
Joao Sousa 304 25.23228706313131

Alexander Zverev 192 30.210194280182193
David Ferrer 1084 15.245050129436047

Tallon Griekspoor 2 114.7891374898585
Stanislas Wawrinka 737 17.773724598962772

Robin Haase 415 22.31723016698542
Thiemo De B

Michael Mmoh 10 84.62593986645679
Christopher Eubanks 7 92.52679312178833

Matthew Ebden 142 33.96354974269963
Gilles Simon 742 17.726041753516554

Jared Donaldson 88 40.789354188116036
Marcos Baghdatis 599 19.298574608243758

Joao Sousa 310 25.038931217956442
Ryan Harrison 238 27.77777777777777

Maximilian Marterer 23 65.92904670306449
Marton Fucsovics 52 49.612380563965935

Jeremy Chardy 465 21.33540373329256
Rogerio Dutra Silva 86 41.14560492637658

Mikael Ymer 12 80.49343113115424
Jan Lennard Struff 167 31.895442368950476

Nicolas Jarry 32 58.97382803159548
Cameron Norrie 11 82.46924442330588

Benoit Paire 336 24.25706528600241
Mischa Zverev 274 26.284415713609377

Liam Broady 10 84.62593986645679
Bjorn Fratangelo 37 56.05834764532697

John Millman 80 42.28364698756727
Peter Gojowczyk 69 44.69380406901229

Robin Haase 420 22.211834896887808
Yuichi Sugita 100 38.85655458615683

Yuki Bhambri 47 51.468163416662996
Mirza Basic 37 56.05834764532697

Leonardo Mayer 304 25.23228706313131


Roberto Carballes Baena 42 53.59211114843642

Grigor Dimitrov 442 21.767923344903863
Malek Jaziri 176 31.2513353152003

Pablo Carreno Busta 241 27.64177743601099
Adrian Mannarino 319 24.75836747175004

Dominic Thiem 307 25.134958416537444
Jozef Kovalik 27 62.5

Stefanos Tsitsipas 31 59.62371171271897
Albert Ramos 358 23.657963567483108

Roberto Bautista Agut 368 23.402188649148904
Pablo Andujar 299 25.397476972508493

David Goffin 346 23.978232232620933
Karen Khachanov 109 37.59915356241083

Martin Klizan 252 27.162313620300182
Feliciano Lopez 881 16.556423238585356

Rafael Nadal 1083 15.250653382594285
Guillermo Garcia Lopez 616 19.085492378198744

Pablo Carreno Busta 242 27.59695893701715
Grigor Dimitrov 443 21.748474668602295

Stefanos Tsitsipas 32 58.97382803159548
Dominic Thiem 308 25.102806224120716

David Goffin 347 23.950960983476705
Roberto Bautista Agut 369 23.377139464898736

Rafael Nadal 1084 15.245050129436047
Martin Klizan 253 27.120152437104903

Stefanos Tsitsipas 33 58.

In [98]:
df_elo_ratings = pd.DataFrame.from_dict(elo_ratings, orient='index')
df_elo_ratings.columns = ['rating']
df_elo_ratings = df_elo_ratings.sort_values(['rating'], ascending=[False])
df_elo_ratings.head

<bound method NDFrame.head of                                       rating
Roger Federer                    2290.950428
Novak Djokovic                   2237.390782
Rafael Nadal                     2237.063988
Andy Murray                      2227.037495
Alexander Zverev                 2128.294149
Juan Martin Del Potro            2120.310120
Robin Soderling                  2099.537556
Kei Nishikori                    2050.131880
David Goffin                     2035.530169
Marin Cilic                      2015.198187
Grigor Dimitrov                  2014.899407
Dominic Thiem                    2009.058244
Jo Wilfried Tsonga               1993.869594
Nick Kyrgios                     1989.431384
Milos Raonic                     1983.651087
Stanislas Wawrinka               1975.130276
Tomas Berdych                    1962.664861
Kevin Anderson                   1940.030931
Andy Roddick                     1938.206319
Hyeon Chung                      1936.364849
Kyle Edmund              

This seems pretty good... it might not match the 538 or tennisabstract ratings, but at least the top players come out on top.

To-do:
* Maybe filter so that only currently players are displayed.
* Add the 538 K value computation: 
* Add the time-off penalty: http://www.tennisabstract.com/blog/2018/05/15/handling-injuries-and-absences-with-tennis-elo/